In [1]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc




def add_layers_anndata(process_type, input_file_h5ad, gene_annot_file, species, SRP_name, resolution, base_folder):


    bins_bed = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.csv', names=['chr', 'start', 'end'])
    bins_bed['bin_id'] = bins_bed.index.tolist()

    bins_bed.to_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv', index=False, header=False, sep='\t')
    if species == 'human':

        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Human/hg38-blacklist.v2.bed'
    else:
        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Mouse/mm10-blacklist.v2.bed'

    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {blacklist_file} -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed")
    blacklist_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'c1', 'c2', 'c3', 'c4'])
    
    
    adata = ad.read_h5ad(f'{input_file_h5ad}')

    data = adata.X + 0.0
    
    if resolution == '1kbp_raw':
    
        data = data.astype('float32')
        
    elif resolution == '10kbp_raw':
    
        data = data.astype('float32')
    else:
        data = data.astype('float64')

        
    
    nan_columns = blacklist_bins['bin_id'].tolist()

    data[:, nan_columns] = np.nan


    chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()

    chrom_index_list  = {}
    for chrom in chr_list:
          st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
          en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
          chrom_index_list[chrom] = list(range(st, en+1))

    chrom_index_list_intra = {}
    for chrom in chr_list:
        index_list = []
        for chrom2 in chr_list:
            if chrom2 != chrom:
                index_list.extend(chrom_index_list[chrom2])

        chrom_index_list_intra[chrom] = index_list

    gtf = read_gtf(gene_annot_file)
    genes = gtf.df.loc[gtf.df['Feature'] == 'gene'].copy()
    genes['gene_id'] = [x.split('.')[0] for x in genes['gene_id']]
    genes['gene_id'].drop_duplicates(inplace=True)

    if not genes['Chromosome'].str.startswith('chr').any():
        genes['Chromosome'] = [f'chr{x}' for x in genes['Chromosome']]

    genes  = genes.set_index('gene_id')

    genes = genes.loc[adata.obs_names.tolist(), :]
    
    genes = genes.reset_index()



    genes[['Chromosome', 'Start', 'End', 'gene_id']].to_csv(f'{base_folder}hi_c_data_processing/data_{species}/gene_info.tsv', index=False, header=False, sep='\t')


    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {base_folder}hi_c_data_processing/data_{species}/gene_info.tsv -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv")
    gene_id_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'st', 'end', 'gene_id', 'c4'])

    
    if process_type == 'intra':

        layer_value_list = [0, 10, 100, 1000, 10000]
        layer_name_list = ['intra']*len(layer_value_list)

    if process_type == 'inter':
        layer_name_list = ['inter']
        layer_value_list = [0]

    if process_type == 'gw':
        layer_value_list = [0, 10, 100, 1000, 10000]
        layer_name_list = ['intra']*len(layer_value_list)
        layer_name_list.append('inter')
        layer_value_list.append(0)



    for layer_type, dist in zip(layer_name_list, layer_value_list):
        
        new_layer_name = f'{process_type}_{layer_type}_{dist}'
        
        if new_layer_name in adata.layers:
            continue
        else:

            mask = np.zeros_like(data, dtype=bool)

        

            for index, row in genes.iterrows():

                if layer_type == 'intra':
                    columns_to_mask = chrom_index_list_intra[row['Chromosome']]
                else:
                    columns_to_mask = chrom_index_list[row['Chromosome']]

                mask[index, columns_to_mask] = True

                if layer_type == 'intra':

                    start_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].min()

                    end_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].max()

                    mask[index, start_index:end_index+1]  = True

                    #for idx in [start_index, end_index]:
                    mask[index, max(0, start_index - dist):min(data.shape[1], end_index + dist+1)] = True




            data_layered = np.where(mask, np.nan, data)



            layer_name = f'{process_type}_{layer_type}_{dist}'

            adata.layers[layer_name] = data_layered

            z_scores = stats.zscore(data_layered, axis=1, nan_policy='omit')


            clipped_z_scores = np.clip(z_scores, -10, 10)



            layer_name = f'{process_type}_{layer_type}_{dist}_z_scores'

            adata.layers[layer_name] = clipped_z_scores



            del z_scores
            del clipped_z_scores
            gc.collect()

            #data_plus_one = data_layered + 1

            #log_transformed_data = np.log1p(data_plus_one)

            del data_layered
            #del data_plus_one
            gc.collect()

            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed'

            #adata.layers[layer_name] = log_transformed_data

            #z_scores = stats.zscore(log_transformed_data, axis=1, nan_policy='omit')

            #clipped_z_scores = np.clip(z_scores, -10, 10)



            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed_z_scores'

            #adata.layers[layer_name] = clipped_z_scores

            #del z_scores
            #del log_transformed_data
            #del clipped_z_scores
            #gc.collect()

            adata.write(f'{input_file_h5ad}', compression="gzip")

INFO:numexpr.utils:Note: detected 192 virtual cores but NumExpr set to maximum of 64, check "NUMEXPR_MAX_THREADS" environment variable.
INFO:numexpr.utils:Note: NumExpr detected 192 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.


In [3]:
add_layers_anndata('gw', '/grid/gillis/data_norepl/lohia/hi_c_data_processing/data_mouse/aggregates/1kbp_raw/max/hic_gene_gw_none_by_allbins_max.h5ad', '/grid/gillis/data_norepl/lohia/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz', 'mouse', 'aggregates', '1kbp_raw', '/grid/gillis/data_norepl/lohia/')



AnnDataReadError: Above error raised while reading key '/layers/gw_intra_0_log_transformed' of type <class 'h5py._hl.dataset.Dataset'> from /.

In [2]:
base_folder = '/grid/gillis/data_norepl/lohia/'
species='human'
resolution='1kbp_raw'
SRP_name='aggregates'
input_file_h5ad='/grid/gillis/data_norepl/lohia/hi_c_data_processing/data_mouse/aggregates/1kbp_raw/max/hic_gene_gw_none_by_allbins_max.h5ad'
gene_annot_file='/grid/gillis/data_norepl/lohia/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz'
process_type='gw'

In [3]:
    bins_bed = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.csv', names=['chr', 'start', 'end'])
    bins_bed['bin_id'] = bins_bed.index.tolist()

    bins_bed.to_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv', index=False, header=False, sep='\t')
    if species == 'human':

        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Human/hg38-blacklist.v2.bed'
    else:
        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Mouse/mm10-blacklist.v2.bed'

    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {blacklist_file} -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed")
    blacklist_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'c1', 'c2', 'c3', 'c4'])
    

In [4]:
adata = ad.read_h5ad(f'/grid/gillis/data_norepl/lohia/hi_c_data_processing/data_human/aggregates/1kbp_raw/max/hic_gene_gw_none_by_allbins_max.h5ad')



In [5]:
adata.layers

Layers with keys: gw_intra_0, gw_intra_0_log_transformed, gw_intra_0_log_transformed_z_scores, gw_intra_0_z_scores

In [6]:
    data = adata.X + 0.0
    
    if resolution == '1kbp_raw':
    
        data = data.astype('float32')
        
    elif resolution == '10kbp_raw':
    
        data = data.astype('float32')
    else:
        data = data.astype('float64')

        
    
    nan_columns = blacklist_bins['bin_id'].tolist()

    data[:, nan_columns] = np.nan


    chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()

    chrom_index_list  = {}
    for chrom in chr_list:
          st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
          en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
          chrom_index_list[chrom] = list(range(st, en+1))

    chrom_index_list_intra = {}
    for chrom in chr_list:
        index_list = []
        for chrom2 in chr_list:
            if chrom2 != chrom:
                index_list.extend(chrom_index_list[chrom2])

        chrom_index_list_intra[chrom] = index_list

    gtf = read_gtf(gene_annot_file)
    genes = gtf.df.loc[gtf.df['Feature'] == 'gene'].copy()
    genes['gene_id'] = [x.split('.')[0] for x in genes['gene_id']]
    genes['gene_id'].drop_duplicates(inplace=True)

    if not genes['Chromosome'].str.startswith('chr').any():
        genes['Chromosome'] = [f'chr{x}' for x in genes['Chromosome']]

    genes  = genes.set_index('gene_id')

    genes = genes.loc[adata.obs_names.tolist(), :]
    
    genes = genes.reset_index()



    genes[['Chromosome', 'Start', 'End', 'gene_id']].to_csv(f'{base_folder}hi_c_data_processing/data_{species}/gene_info.tsv', index=False, header=False, sep='\t')


    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {base_folder}hi_c_data_processing/data_{species}/gene_info.tsv -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv")
    gene_id_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'st', 'end', 'gene_id', 'c4'])

    


In [7]:
    if process_type == 'intra':

        layer_value_list = [0, 10, 100, 1000, 10000]
        layer_name_list = ['intra']*len(layer_value_list)

    if process_type == 'inter':
        layer_name_list = ['inter']
        layer_value_list = [0]

    if process_type == 'gw':
        layer_value_list = [0, 10, 100, 1000, 10000]
        layer_name_list = ['intra']*len(layer_value_list)
        layer_name_list.append('inter')
        layer_value_list.append(0)



    for layer_type, dist in zip(layer_name_list, layer_value_list):
        
        new_layer_name = f'{process_type}_{layer_type}_{dist}'
        
        if new_layer_name in adata.layers:
            continue
        else:

            mask = np.zeros_like(data, dtype=bool)

        

            for index, row in genes.iterrows():

                if layer_type == 'intra':
                    columns_to_mask = chrom_index_list_intra[row['Chromosome']]
                else:
                    columns_to_mask = chrom_index_list[row['Chromosome']]

                mask[index, columns_to_mask] = True

                if layer_type == 'intra':

                    start_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].min()

                    end_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].max()

                    mask[index, start_index:end_index+1]  = True

                    #for idx in [start_index, end_index]:
                    mask[index, max(0, start_index - dist):min(data.shape[1], end_index + dist+1)] = True




            data_layered = np.where(mask, np.nan, data)



            layer_name = f'{process_type}_{layer_type}_{dist}'

            adata.layers[layer_name] = data_layered

            z_scores = stats.zscore(data_layered, axis=1, nan_policy='omit')


            clipped_z_scores = np.clip(z_scores, -10, 10)



            layer_name = f'{process_type}_{layer_type}_{dist}_z_scores'

            adata.layers[layer_name] = clipped_z_scores



            del z_scores
            del clipped_z_scores
            gc.collect()

            #data_plus_one = data_layered + 1

            #log_transformed_data = np.log1p(data_plus_one)

            del data_layered
            #del data_plus_one
            gc.collect()

            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed'

            #adata.layers[layer_name] = log_transformed_data

            #z_scores = stats.zscore(log_transformed_data, axis=1, nan_policy='omit')

            #clipped_z_scores = np.clip(z_scores, -10, 10)



            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed_z_scores'

            #adata.layers[layer_name] = clipped_z_scores

            #del z_scores
            #del log_transformed_data
            #del clipped_z_scores
            #gc.collect()

            adata.write(f'{input_file_h5ad}', compression="gzip")

OSError: Unable to create file (file signature not found)

In [ ]:
if [[ "$species" == "human" ]]
then
CHROMS=/grid/gillis/data_norepl/nfox/genomes/homo_sapiens_38/hg38.chrom.sizes 
chrom_list="chr1,chr2,chr3,chr4,chr5,chr6,chr7,chr8,chr9,chr10,chr11,chr12,chr13,chr14,chr15,chr16,chr17,chr18,chr19,chr20,chr21,chr22"
chrom_list_2="chr1 chr2 chr3 chr4 chr5 chr6 chr7 chr8 chr9 chr10 chr11 chr12 chr13 chr14 chr15 chr16 chr17 chr18 chr19 chr20 chr21 chr22"
GENOME="gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz"
EXP_NETWORKS="human_prioAggNet.hdf5"

elif [[ "$species" == "mouse" ]]
then
CHROMS=/grid/gillis/data_norepl/nfox/genomes/mus_musculus_10/mm10.chrom.sizes
GENOME="Mus_musculus.GRCm38.94.gtf.gz"
EXP_NETWORKS="mouse_prioAggNet.hdf5"
chrom_list="chr1,chr2,chr3,chr4,chr5,chr6,chr7,chr8,chr9,chr10,chr11,chr12,chr13,chr14,chr15,chr16,chr17,chr18,chr19"
chrom_list_2="chr1 chr2 chr3 chr4 chr5 chr6 chr7 chr8 chr9 chr10 chr11 chr12 chr13 chr14 chr15 chr16 chr17 chr18 chr19"


In [ ]:
add_layers_anndata(process_type, input_file_h5ad, gene_annot_file, species, SRP_name, resolution, base_folder)



In [ ]:

ice_type='none'

base_path='/grid/gillis/data_norepl/lohia/'


        
    python ${software_path}/add_contact_norm_layers.py \
    --process_type ${process} \
    --species ${species} \
    --input_file_h5ad /grid/gillis/data_norepl/lohia/hi_c_data_processing/data_mouse/aggregates/10kbp_raw/max/hic_gene_gw_none_by_allbins_max.h5ad \
    --base_path $base_path \
    --resolution $NETWORK \
    --SRP $SRP_name \
    --gene_annot_file ${base_folder}/lohia/hi_c_data_processing/genomes_jlee/${GENOME}
    

